# Characterizing CpG Methylation

To describe general metylation trends, irrespective of pCO<sub>2</sub> treatment in *C. virginica* gonad sequence data, I need to characterize individual CpG loci. Gavery and Roberts (2013) and Olson and Roberts (2013) define a CpG locus as methylated if at least half of the reads remained unconverted after bisulfite treatment. I will use information in a master `.cov` file to identify methylated CpG loci.

1. Download coverage file
2. Limit to 5x coverage
3. Characterize methylation levels for loci
4. Characterize loci locations

## 0. Prepare for analyses

## 0a. Set working directory

In [1]:
pwd

'/Users/yaamini/Documents/yaamini-virginica/notebooks'

In [2]:
cd ../analyses/

/Users/yaamini/Documents/yaamini-virginica/analyses


In [3]:
!mkdir 2019-03-18-Characterizing-CpG-Methylation

In [3]:
cd 2019-03-18-Characterizing-CpG-Methylation/

/Users/yaamini/Documents/yaamini-virginica/analyses/2019-03-18-Characterizing-CpG-Methylation


In [17]:
pwd

'/Users/yaamini/Documents/yaamini-virginica/analyses/2019-03-18-Characterizing-CpG-Methylation'

## 1. Obtain coverage files

In [4]:
#Download file from gannet. This file is a concatenation of coverage and methylation information for all samples
!wget http://gannet.fish.washington.edu/Atumefaciens/20190312_cvir_gonad_bismark/total_reads_bismark/cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov.gz

--2019-04-09 14:41:39--  http://gannet.fish.washington.edu/Atumefaciens/20190312_cvir_gonad_bismark/total_reads_bismark/cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov.gz
Resolving gannet.fish.washington.edu... 128.95.149.52
Connecting to gannet.fish.washington.edu|128.95.149.52|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 94181669 (90M) [application/x-gzip]
Saving to: 'cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov.gz'

cvir_bsseq_all_pe_R 100%[===================>]  89.82M  75.1MB/s    in 1.2s    

2019-04-09 14:41:40 (75.1 MB/s) - 'cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov.gz' saved [94181669/94181669]



In [8]:
#Unzip the coverage file
!gunzip *cov.gz

In [9]:
#Confirm file was unzipped
!ls *cov

cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov


In [4]:
#See what the file looks like. 
#Columns: <chromosome> <start position> <end position> <methylation percentage> <count methylated> <count unmethylated>
!head cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov

NC_007175.2	49	49	1.25	2	158
NC_007175.2	50	50	0	0	15
NC_007175.2	51	51	1.18343195266272	2	167
NC_007175.2	52	52	0	0	18
NC_007175.2	88	88	1.02459016393443	5	483
NC_007175.2	89	89	1.38888888888889	5	355
NC_007175.2	100	100	0	0	1
NC_007175.2	129	129	0	0	1
NC_007175.2	147	147	1.99115044247788	18	886
NC_007175.2	148	148	2.29885057471264	6	255


In [6]:
#See how many loci have data
!awk '{if ($5+$6 >= 1) { print $1, $2-1, $3, $4, $5+$6}}' cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov \
| wc -l

 14026131


14,026,131 CpGs have data, which is close to the 14,458,703 CG motifs in the *C. virginica* genome.

## 2. Limit to 5x coverage

In [11]:
#If total coverage (count methylated + unmethylated) is greater than 5
#then print the chromosome, start pos -1, stop pos, percent methylation, and total coverage
#Save output as new file
!awk '{if ($5+$6 >= 5) { print $1, $2-1, $3, $4, $5+$6}}' cvir_bsseq_all_pe_R1_bismark_bt2_pe.bismark.cov \
> 2019-04-09-All-5x-CpGs.bedgraph

In [12]:
#Check columns for one of the file: <chromosome> <start position> <stop position> <percent methylation> <coverage>
!head 2019-04-09-All-5x-CpGs.bedgraph

NC_007175.2 48 49 1.25 160
NC_007175.2 49 50 0 15
NC_007175.2 50 51 1.18343195266272 169
NC_007175.2 51 52 0 18
NC_007175.2 87 88 1.02459016393443 488
NC_007175.2 88 89 1.38888888888889 360
NC_007175.2 146 147 1.99115044247788 904
NC_007175.2 147 148 2.29885057471264 261
NC_007175.2 173 174 0 5
NC_007175.2 192 193 1.25786163522013 795


In [58]:
#Count loci with 5x coverage
!wc -l 2019-04-09-All-5x-CpGs.bedgraph

 4304257 2019-04-09-All-5x-CpGs.bedgraph


I have data for 4,304,257 CpG loci with 5x coverge.

In [59]:
#Replace delimiters to save .bedgraph as .csv
!awk '{print $1","$2","$3","$4 }' 2019-04-09-All-5x-CpGs.bedgraph \
> 2019-04-09-All-5x-CpGs.csv

In [60]:
#Confirm .csv creation
!head 2019-04-09-All-5x-CpGs.csv

NC_007175.2,48,49,1.25
NC_007175.2,49,50,0
NC_007175.2,50,51,1.18343195266272
NC_007175.2,51,52,0
NC_007175.2,87,88,1.02459016393443
NC_007175.2,88,89,1.38888888888889
NC_007175.2,146,147,1.99115044247788
NC_007175.2,147,148,2.29885057471264
NC_007175.2,173,174,0
NC_007175.2,192,193,1.25786163522013


## 3. Characterize methylation levels for loci

Olson and Roberts (2014) define the following categories for CpG methylation:

- Methylated (50% methylation and above)
- Sparsely methylated (0-50% methylated)
- Unmethylated (0% methylation)

I will slightly modify this since I have multiple samples:

- Methylated (50% methylation and above)
- Sparsely methylated (10-50% methylated)
- Unmethylated (10% methylation and below)

### 3a. Methylated loci

In [19]:
#If percent methylation is greater or equal to 50, then save the loci information
!awk '{if ($4 >= 50) { print $1, $2, $3, $4 }}' 2019-04-09-All-5x-CpGs.bedgraph \
> 2019-04-09-All-5x-CpG-Loci-Methylated.bedgraph

In [48]:
#Confirm methylated loci were saved
!head 2019-04-09-All-5x-CpG-Loci-Methylated.bedgraph

NC_035780.1 9253 9254 60
NC_035780.1 9637 9638 60
NC_035780.1 9657 9658 50
NC_035780.1 10089 10090 71.4285714285714
NC_035780.1 10331 10332 80
NC_035780.1 11692 11693 80
NC_035780.1 11706 11707 80
NC_035780.1 11711 11712 80
NC_035780.1 12686 12687 69.2307692307692
NC_035780.1 12758 12759 80


In [21]:
#Count methylated loci
!wc -l 2019-04-09-All-5x-CpG-Loci-Methylated.bedgraph

 3181904 2019-04-09-All-5x-CpG-Loci-Methylated.bedgraph


In [53]:
#Replace delimiters to save .bedgraph as .csv
!awk '{print $1","$2","$3","$4 }' 2019-04-09-All-5x-CpG-Loci-Methylated.bedgraph \
> 2019-04-09-All-5x-CpG-Loci-Methylated.csv

In [54]:
#Check .csv was saved
!head 2019-04-09-All-5x-CpG-Loci-Methylated.csv

NC_035780.1,9253,9254,60
NC_035780.1,9637,9638,60
NC_035780.1,9657,9658,50
NC_035780.1,10089,10090,71.4285714285714
NC_035780.1,10331,10332,80
NC_035780.1,11692,11693,80
NC_035780.1,11706,11707,80
NC_035780.1,11711,11712,80
NC_035780.1,12686,12687,69.2307692307692
NC_035780.1,12758,12759,80


### 3b. Sparsely methylated loci

In [33]:
%%bash
awk '{if ($4 < 50) { print $1, $2, $3, $4}}' 2019-04-09-All-5x-CpGs.bedgraph \
| awk '{if ($4 > 10) { print $1, $2, $3, $4 }}' \
> 2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bedgraph

In [34]:
#Confirm sparsely methylated loci were saved
!head 2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bedgraph

NC_007175.2 1506 1507 16.6666666666667
NC_007175.2 1820 1821 20
NC_007175.2 2128 2129 11.7647058823529
NC_007175.2 4841 4842 15
NC_007175.2 13069 13070 20
NC_035780.1 421 422 14.2857142857143
NC_035780.1 1101 1102 12.5
NC_035780.1 1540 1541 16.6666666666667
NC_035780.1 3468 3469 16.6666666666667
NC_035780.1 9254 9255 28.5714285714286


In [35]:
#Count sparsely methylated loci
!wc -l 2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bedgraph

  481788 2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bedgraph


### 3c. Unmethylated loci

In [36]:
!awk '{if ($4 <= 10) { print $1, $2, $3, $4 }}' 2019-04-09-All-5x-CpGs.bedgraph \
> 2019-04-09-All-5x-CpG-Loci-Unmethylated.bedgraph

In [37]:
#Confirm unmethylated loci were saved
!head 2019-04-09-All-5x-CpG-Loci-Unmethylated.bedgraph

NC_007175.2 48 49 1.25
NC_007175.2 49 50 0
NC_007175.2 50 51 1.18343195266272
NC_007175.2 51 52 0
NC_007175.2 87 88 1.02459016393443
NC_007175.2 88 89 1.38888888888889
NC_007175.2 146 147 1.99115044247788
NC_007175.2 147 148 2.29885057471264
NC_007175.2 173 174 0
NC_007175.2 192 193 1.25786163522013


In [38]:
#Count unmethylated loci
!wc -l 2019-04-09-All-5x-CpG-Loci-Unmethylated.bedgraph

  640565 2019-04-09-All-5x-CpG-Loci-Unmethylated.bedgraph


## 4. Characterize loci locations

My final step is to characterize the location of various loci categories in the genome. I will use `intersectBed` to find overlaps between all 5x CpGs, methylated loci, sparsely methylated loci, and unmethylated loci with exons, introns, mRNA coding regions, transposable elements, and putative promoter regions.

### 4a. Create `.bed` files

#### All 5x CpGs

In [69]:
%%bash
awk '{print $1"\t"$2"\t"$3}' 2019-04-09-All-5x-CpGs.bedgraph \
> 2019-04-09-All-5x-CpGs.bed

In [70]:
#Confirm file creation
!head 2019-04-09-All-5x-CpGs.bed

NC_007175.2	48	49
NC_007175.2	49	50
NC_007175.2	50	51
NC_007175.2	51	52
NC_007175.2	87	88
NC_007175.2	88	89
NC_007175.2	146	147
NC_007175.2	147	148
NC_007175.2	173	174
NC_007175.2	192	193


#### Methylated loci

In [8]:
%%bash
awk '{print $1"\t"$2"\t"$3}' 2019-04-09-All-5x-CpG-Loci-Methylated.bedgraph \
> 2019-04-09-All-5x-CpG-Loci-Methylated.bed

In [47]:
#Confirm file creation
!head 2019-04-09-All-5x-CpG-Loci-Methylated.bed

NC_035780.1	9253	9254
NC_035780.1	9637	9638
NC_035780.1	9657	9658
NC_035780.1	10089	10090
NC_035780.1	10331	10332
NC_035780.1	11692	11693
NC_035780.1	11706	11707
NC_035780.1	11711	11712
NC_035780.1	12686	12687
NC_035780.1	12758	12759


#### Sparsely methylated loci

In [5]:
%%bash
awk '{print $1"\t"$2"\t"$3}' 2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bedgraph \
> 2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bed

In [6]:
#Confirm file creation
!head 2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bed

NC_007175.2	1506	1507
NC_007175.2	1820	1821
NC_007175.2	2128	2129
NC_007175.2	4841	4842
NC_007175.2	13069	13070
NC_035780.1	421	422
NC_035780.1	1101	1102
NC_035780.1	1540	1541
NC_035780.1	3468	3469
NC_035780.1	9254	9255


#### Unmethylated loci

In [7]:
%%bash
awk '{print $1"\t"$2"\t"$3}' 2019-04-09-All-5x-CpG-Loci-Unmethylated.bedgraph \
> 2019-04-09-All-5x-CpG-Loci-Unmethylated.bed

In [8]:
#Confirm file creation
!head 2019-04-09-All-5x-CpG-Loci-Unmethylated.bed

NC_007175.2	48	49
NC_007175.2	49	50
NC_007175.2	50	51
NC_007175.2	51	52
NC_007175.2	87	88
NC_007175.2	88	89
NC_007175.2	146	147
NC_007175.2	147	148
NC_007175.2	173	174
NC_007175.2	192	193


### 4b. Set variable paths

In [10]:
bedtoolsDirectory = "/Users/Shared/bioinformatics/bedtools2/bin/"

In [71]:
all5xCpGs = "2019-04-09-All-5x-CpGs.bed"

In [10]:
methylatedLoci = "2019-04-09-All-5x-CpG-Loci-Methylated.bed"

In [17]:
sparselyMethylatedLoci = "2019-04-09-All-5x-CpG-Loci-Sparsely-Methylated.bed"

In [18]:
unmethylatedLoci = "2019-04-09-All-5x-CpG-Loci-Unmethylated.bed"

In [11]:
exonList = "../2018-11-01-DML-and-DMR-Analysis/C_virginica-3.0_Gnomon_exon.bed"

In [12]:
intronList = "../2018-11-01-DML-and-DMR-Analysis/C_virginica-3.0_intron.bed"

In [13]:
mRNAList = "../2018-11-01-DML-and-DMR-Analysis/C_virginica-3.0_Gnomon_mRNA.gff3"

In [14]:
transposableElementsAll = "../2018-11-01-DML-and-DMR-Analysis/C_virginica-3.0_TE-all.gff"

In [15]:
transposableElementsCg = "../2018-11-01-DML-and-DMR-Analysis/C_virginica-3.0_TE-Cg.gff"

In [16]:
putativePromoters = "../2018-11-01-DML-and-DMR-Analysis/2018-11-14-Flanking-Analysis/2018-11-15-mRNA-Upstream-Flanks.bed"

### 4c. Exons

#### All 5x CpGs

In [72]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {all5xCpGs} \
-b {exonList} \
| wc -l
!echo "all 5x CpG loci overlaps with exons"

 1366779
all 5x CpG loci overlaps with exons


In [73]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {all5xCpGs} \
-b {exonList} \
> 2019-04-10-All5xCpGs-Exon.txt

In [74]:
!head 2019-04-10-All5xCpGs-Exon.txt

NC_035780.1	28992	28993	NC_035780.1	28961	29073
NC_035780.1	29001	29002	NC_035780.1	28961	29073
NC_035780.1	30723	30724	NC_035780.1	30524	31557
NC_035780.1	30765	30766	NC_035780.1	30524	31557
NC_035780.1	30811	30812	NC_035780.1	30524	31557
NC_035780.1	30906	30907	NC_035780.1	30524	31557
NC_035780.1	30932	30933	NC_035780.1	30524	31557
NC_035780.1	30935	30936	NC_035780.1	30524	31557
NC_035780.1	31017	31018	NC_035780.1	30524	31557
NC_035780.1	31018	31019	NC_035780.1	30524	31557


#### Methylated loci

In [19]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {methylatedLoci} \
-b {exonList} \
| wc -l
!echo "methylated loci overlaps with exons"

 1013691
methylated loci overlaps with exons


In [20]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {methylatedLoci} \
-b {exonList} \
> 2019-04-10-MethLoci-Exon.txt

In [21]:
!head 2019-04-10-MethLoci-Exon.txt

NC_035780.1	100558	100559	NC_035780.1	100554	100661
NC_035780.1	100559	100560	NC_035780.1	100554	100661
NC_035780.1	100575	100576	NC_035780.1	100554	100661
NC_035780.1	100576	100577	NC_035780.1	100554	100661
NC_035780.1	100581	100582	NC_035780.1	100554	100661
NC_035780.1	100582	100583	NC_035780.1	100554	100661
NC_035780.1	100634	100635	NC_035780.1	100554	100661
NC_035780.1	100635	100636	NC_035780.1	100554	100661
NC_035780.1	100643	100644	NC_035780.1	100554	100661
NC_035780.1	100644	100645	NC_035780.1	100554	100661


#### Sparsely methylated loci

In [19]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {sparselyMethylatedLoci} \
-b {exonList} \
| wc -l
!echo "sparsely methylated loci overlaps with exons"

  105871
sparsely methylated loci overlaps with exons


In [20]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {sparselyMethylatedLoci} \
-b {exonList} \
> 2019-04-10-SparseMethLoci-Exon.txt

In [21]:
!head 2019-04-10-SparseMethLoci-Exon.txt

NC_035780.1	31078	31079	NC_035780.1	30524	31557
NC_035780.1	85755	85756	NC_035780.1	85606	85777
NC_035780.1	94754	94755	NC_035780.1	94571	95254
NC_035780.1	106236	106237	NC_035780.1	106004	106460
NC_035780.1	204528	204529	NC_035780.1	204243	204795
NC_035780.1	207401	207402	NC_035780.1	207388	207743
NC_035780.1	207423	207424	NC_035780.1	207388	207743
NC_035780.1	207472	207473	NC_035780.1	207388	207743
NC_035780.1	223409	223410	NC_035780.1	223311	223637
NC_035780.1	223416	223417	NC_035780.1	223311	223637


#### Unmethylated loci

In [22]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {unmethylatedLoci} \
-b {exonList} \
| wc -l
!echo "unmethylated loci overlaps with exons"

  247217
unmethylated loci overlaps with exons


In [23]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {unmethylatedLoci} \
-b {exonList} \
> 2019-04-10-UnMethLoci-Exon.txt

In [24]:
!head 2019-04-10-UnMethLoci-Exon.txt

NC_035780.1	28992	28993	NC_035780.1	28961	29073
NC_035780.1	29001	29002	NC_035780.1	28961	29073
NC_035780.1	30723	30724	NC_035780.1	30524	31557
NC_035780.1	30765	30766	NC_035780.1	30524	31557
NC_035780.1	30811	30812	NC_035780.1	30524	31557
NC_035780.1	30906	30907	NC_035780.1	30524	31557
NC_035780.1	30932	30933	NC_035780.1	30524	31557
NC_035780.1	30935	30936	NC_035780.1	30524	31557
NC_035780.1	31017	31018	NC_035780.1	30524	31557
NC_035780.1	31018	31019	NC_035780.1	30524	31557


### 4d. Introns

#### All 5x CpG

In [75]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {all5xCpGs} \
-b {intronList} \
| wc -l
!echo "all 5x CpG loci overlaps with introns"

 1811271
all 5x CpG loci overlaps with introns


In [76]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {all5xCpGs} \
-b {intronList} \
> 2019-04-10-All5xCpGs-Intron.txt

In [77]:
!head 2019-04-10-All5xCpGs-Intron.txt

NC_035780.1	29412	29413	NC_035780.1	29074	30524
NC_035780.1	31940	31941	NC_035780.1	31888	31977
NC_035780.1	44372	44373	NC_035780.1	44359	45913
NC_035780.1	45142	45143	NC_035780.1	44359	45913
NC_035780.1	45542	45543	NC_035780.1	44359	45913
NC_035780.1	46515	46516	NC_035780.1	46507	64123
NC_035780.1	47583	47584	NC_035780.1	46507	64123
NC_035780.1	47590	47591	NC_035780.1	46507	64123
NC_035780.1	47651	47652	NC_035780.1	46507	64123
NC_035780.1	47679	47680	NC_035780.1	46507	64123


#### Methylated loci

In [22]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {methylatedLoci} \
-b {intronList} \
| wc -l
!echo "methylated loci overlaps with introns"

 1448786
methylated loci overlaps with introns


In [23]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {methylatedLoci} \
-b {intronList} \
> 2019-04-10-MethLoci-Intron.txt

In [24]:
!head 2019-04-10-MethLoci-Intron.txt

NC_035780.1	29412	29413	NC_035780.1	29074	30524
NC_035780.1	87531	87532	NC_035780.1	85778	88423
NC_035780.1	87541	87542	NC_035780.1	85778	88423
NC_035780.1	87590	87591	NC_035780.1	85778	88423
NC_035780.1	87595	87596	NC_035780.1	85778	88423
NC_035780.1	100664	100665	NC_035780.1	100662	104929
NC_035780.1	100665	100666	NC_035780.1	100662	104929
NC_035780.1	100917	100918	NC_035780.1	100662	104929
NC_035780.1	100975	100976	NC_035780.1	100662	104929
NC_035780.1	101305	101306	NC_035780.1	100662	104929


#### Sparsely methylated loci

In [25]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {sparselyMethylatedLoci} \
-b {intronList} \
| wc -l
!echo "sparsely methylated loci overlaps with introns"

  201553
sparsely methylated loci overlaps with introns


In [26]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {sparselyMethylatedLoci} \
-b {intronList} \
> 2019-04-10-SparseMethLoci-Intron.txt

In [27]:
!head 2019-04-10-SparseMethLoci-Intron.txt

NC_035780.1	45142	45143	NC_035780.1	44359	45913
NC_035780.1	45542	45543	NC_035780.1	44359	45913
NC_035780.1	48914	48915	NC_035780.1	46507	64123
NC_035780.1	48928	48929	NC_035780.1	46507	64123
NC_035780.1	48940	48941	NC_035780.1	46507	64123
NC_035780.1	87599	87600	NC_035780.1	85778	88423
NC_035780.1	87607	87608	NC_035780.1	85778	88423
NC_035780.1	103272	103273	NC_035780.1	100662	104929
NC_035780.1	104332	104333	NC_035780.1	100662	104929
NC_035780.1	105767	105768	NC_035780.1	105615	106004


#### Unmethylated loci

In [31]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {unmethylatedLoci} \
-b {intronList} \
| wc -l
!echo "unmethylated loci overlaps with introns"

  160932
unmethylated loci overlaps with introns


In [29]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {unmethylatedLoci} \
-b {intronList} \
> 2019-04-10-UnMethLoci-Intron.txt

In [30]:
!head 2019-04-10-UnMethLoci-Intron.txt

NC_035780.1	31940	31941	NC_035780.1	31888	31977
NC_035780.1	44372	44373	NC_035780.1	44359	45913
NC_035780.1	46515	46516	NC_035780.1	46507	64123
NC_035780.1	47583	47584	NC_035780.1	46507	64123
NC_035780.1	47590	47591	NC_035780.1	46507	64123
NC_035780.1	47651	47652	NC_035780.1	46507	64123
NC_035780.1	47679	47680	NC_035780.1	46507	64123
NC_035780.1	48094	48095	NC_035780.1	46507	64123
NC_035780.1	48108	48109	NC_035780.1	46507	64123
NC_035780.1	48114	48115	NC_035780.1	46507	64123


### 4e. mRNA

#### All 5x CpGs

In [78]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {all5xCpGs} \
-b {mRNAList} \
| wc -l
!echo "all 5x CpG loci overlaps with mRNA coding regions"

 3140744
all 5x CpG loci overlaps with mRNA coding regions


In [79]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {all5xCpGs} \
-b {mRNAList} \
> 2019-04-10-All5xCpGs-mRNA.txt

In [80]:
!head -n 1 2019-04-10-All5xCpGs-mRNA.txt

NC_035780.1	28992	28993	NC_035780.1	Gnomon	mRNA	28961	33324	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1


In [81]:
!cut -f12 2019-04-10-All5xCpGs-mRNA.txt| sort | uniq -c > 2019-04-10-Unique-Genes-in-All5xCpGs-mRNA-Overlap.txt

In [82]:
!head -n 1 2019-04-10-Unique-Genes-in-All5xCpGs-mRNA-Overlap.txt

 107 ID=rna10000;Parent=gene5866;Dbxref=GeneID:111121983,Genbank:XM_022463489.1;Name=XM_022463489.1;gbkey=mRNA;gene=LOC111121983;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 3 samples with support for all annotated introns;product=sodium-coupled neutral amino acid transporter 9-like%2C transcript variant X4;transcript_id=XM_022463489.1


In [83]:
!wc -l 2019-04-10-Unique-Genes-in-All5xCpGs-mRNA-Overlap.txt

   54619 2019-04-10-Unique-Genes-in-All5xCpGs-mRNA-Overlap.txt


The 5x CpG loci overlap with 54,619 unique genes.

#### Methylated loci

In [25]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {methylatedLoci} \
-b {mRNAList} \
| wc -l
!echo "methylated loci overlaps with mRNA coding regions"

 2437901
methylated loci overlaps with mRNA coding regions


In [26]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {methylatedLoci} \
-b {mRNAList} \
> 2019-04-10-MethLoci-mRNA.txt

In [31]:
!head -n 1 2019-04-10-MethLoci-mRNA.txt

NC_035780.1	29412	29413	NC_035780.1	Gnomon	mRNA	28961	33324	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1


In [32]:
!cut -f12 2019-04-10-MethLoci-mRNA.txt| sort | uniq -c > 2019-04-10-Unique-Genes-in-MethLoci-mRNA-Overlap.txt

In [33]:
!head -n 1 2019-04-10-Unique-Genes-in-MethLoci-mRNA-Overlap.txt

  95 ID=rna10000;Parent=gene5866;Dbxref=GeneID:111121983,Genbank:XM_022463489.1;Name=XM_022463489.1;gbkey=mRNA;gene=LOC111121983;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 3 samples with support for all annotated introns;product=sodium-coupled neutral amino acid transporter 9-like%2C transcript variant X4;transcript_id=XM_022463489.1


In [34]:
!wc -l 2019-04-10-Unique-Genes-in-MethLoci-mRNA-Overlap.txt

   44505 2019-04-10-Unique-Genes-in-MethLoci-mRNA-Overlap.txt


Methylated loci overlap with 44,505 unique genes.

#### Sparsely methylated loci

In [32]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {sparselyMethylatedLoci} \
-b {mRNAList} \
| wc -l
!echo "sparsely methylated loci overlaps with mRNA coding regions"

  303890
sparsely methylated loci overlaps with mRNA coding regions


In [33]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {sparselyMethylatedLoci} \
-b {mRNAList} \
> 2019-04-10-SparseMethLoci-mRNA.txt

In [34]:
!head -n 1 2019-04-10-SparseMethLoci-mRNA.txt

NC_035780.1	31078	31079	NC_035780.1	Gnomon	mRNA	28961	33324	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1


In [35]:
!cut -f12 2019-04-10-SparseMethLoci-mRNA.txt| sort | uniq -c > 2019-04-10-Unique-Genes-in-SparseMethLoci-mRNA-Overlap.txt

In [36]:
!head -n 1 2019-04-10-Unique-Genes-in-SparseMethLoci-mRNA-Overlap.txt

   8 ID=rna10000;Parent=gene5866;Dbxref=GeneID:111121983,Genbank:XM_022463489.1;Name=XM_022463489.1;gbkey=mRNA;gene=LOC111121983;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 3 samples with support for all annotated introns;product=sodium-coupled neutral amino acid transporter 9-like%2C transcript variant X4;transcript_id=XM_022463489.1


In [37]:
!wc -l 2019-04-10-Unique-Genes-in-SparseMethLoci-mRNA-Overlap.txt

   47243 2019-04-10-Unique-Genes-in-SparseMethLoci-mRNA-Overlap.txt


Sparsely methylated loci overlap with 47243 unique genes.

#### Unmethylated loci

In [39]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {unmethylatedLoci} \
-b {mRNAList} \
| wc -l
!echo "unmethylated loci overlaps with mRNA coding regions"

  398953
unmethylated loci overlaps with mRNA coding regions


In [40]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {unmethylatedLoci} \
-b {mRNAList} \
> 2019-04-10-UnMethLoci-mRNA.txt

In [41]:
!head -n 1 2019-04-10-UnMethLoci-mRNA.txt

NC_035780.1	28992	28993	NC_035780.1	Gnomon	mRNA	28961	33324	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1


In [42]:
!cut -f12 2019-04-10-UnMethLoci-mRNA.txt| sort | uniq -c > 2019-04-10-Unique-Genes-in-UnMethLoci-mRNA-Overlap.txt

In [43]:
!head -n 1 2019-04-10-Unique-Genes-in-UnMethLoci-mRNA-Overlap.txt

   4 ID=rna10000;Parent=gene5866;Dbxref=GeneID:111121983,Genbank:XM_022463489.1;Name=XM_022463489.1;gbkey=mRNA;gene=LOC111121983;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 3 samples with support for all annotated introns;product=sodium-coupled neutral amino acid transporter 9-like%2C transcript variant X4;transcript_id=XM_022463489.1


In [44]:
!wc -l 2019-04-10-Unique-Genes-in-UnMethLoci-mRNA-Overlap.txt

   47584 2019-04-10-Unique-Genes-in-UnMethLoci-mRNA-Overlap.txt


Unmethylated loci overlap with 47584 unique genes.

### 4f. Transposable elements (all)

#### All 5x CpGs

In [84]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {all5xCpGs} \
-b {transposableElementsAll} \
| wc -l
!echo "all 5x CpG loci overlaps with transposable elements (all)"

 1011883
all 5x CpG loci overlaps with transposable elements (all)


In [85]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {all5xCpGs} \
-b {transposableElementsAll} \
> 2019-04-10-All5xCpGs-TE-All.txt

In [86]:
!head 2019-04-10-All5xCpGs-TE-All.txt

NC_007175.2	263	264	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	264	265	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	265	266	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	266	267	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	295	296	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	331	332	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	332	333	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	366	367	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	367	368	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	397	398

#### Methylated loci

In [35]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {methylatedLoci} \
-b {transposableElementsAll} \
| wc -l
!echo "methylated loci overlaps with transposable elements (all)"

  755222
methylated loci overlaps with transposable elements (all)


In [36]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {methylatedLoci} \
-b {transposableElementsAll} \
> 2019-04-10-MethLoci-TE-All.txt

In [37]:
!head 2019-04-10-MethLoci-TE-All.txt

NC_035780.1	9253	9254	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	19631	19632	NC_035780.1	RepeatMasker	similarity	19431	19866	23.3	-	.	Target "Motif:Crypton-N19_CGi" 580 1033
NC_035780.1	19741	19742	NC_035780.1	RepeatMasker	similarity	19431	19866	23.3	-	.	Target "Motif:Crypton-N19_CGi" 580 1033
NC_035780.1	37557	37558	NC_035780.1	RepeatMasker	similarity	37557	37890	12.9	+	.	Target "Motif:BivaMD-SINE1_CrVi" 1 337
NC_035780.1	37581	37582	NC_035780.1	RepeatMasker	similarity	37557	37890	12.9	+	.	Target "Motif:BivaMD-SINE1_CrVi" 1 337
NC_035780.1	37604	37605	NC_035780.1	RepeatMasker	similarity	37557	37890	12.9	+	.	Target "Motif:BivaMD-SINE1_CrVi" 1 337
NC_035780.1	37611	37612	NC_035780.1	RepeatMasker	similarity	37557	37890	12.9	+	.	Target "Motif:BivaMD-SINE1_CrVi" 1 337
NC_035780.1	37618	37619	NC_035780.1	RepeatMasker	similarity	37557	37890	12.9	+	.	Target "Motif:BivaMD-SINE1_CrVi" 1 337
NC_035780.1	37622	37623	NC_035780.1	RepeatMasker	

#### Sparsely methylated loci

In [45]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {sparselyMethylatedLoci} \
-b {transposableElementsAll} \
| wc -l
!echo "sparsely methylated loci overlaps with transposable elements (all)"

  155293
sparsely methylated loci overlaps with transposable elements (all)


In [46]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {sparselyMethylatedLoci} \
-b {transposableElementsAll} \
> 2019-04-10-SparseMethLoci-TE-All.txt

In [47]:
!head 2019-04-10-SparseMethLoci-TE-All.txt

NC_007175.2	1820	1821	NC_007175.2	RepeatMasker	similarity	1728	1947	26.1	-	.	Target "Motif:REP-6_LMi" 14320 14534
NC_007175.2	2128	2129	NC_007175.2	RepeatMasker	similarity	2129	2367	20.5	-	.	Target "Motif:REP-6_LMi" 13886 14118
NC_035780.1	9254	9255	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9266	9267	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9267	9268	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9297	9298	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9298	9299	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9301	9302	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9302	9303	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780

#### Unmethylated loci

In [48]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {unmethylatedLoci} \
-b {transposableElementsAll} \
| wc -l
!echo "unmethylated loci overlaps with transposable elements (all)"

  101368
unmethylated loci overlaps with transposable elements (all)


In [49]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {unmethylatedLoci} \
-b {transposableElementsAll} \
> 2019-04-10-UnMethLoci-TE-All.txt

In [50]:
!head 2019-04-10-UnMethLoci-TE-All.txt

NC_007175.2	263	264	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	264	265	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	265	266	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	266	267	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	295	296	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	331	332	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	332	333	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	366	367	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	367	368	NC_007175.2	RepeatMasker	similarity	262	1389	31.1	+	.	Target "Motif:REP-6_LMi" 2920 4055
NC_007175.2	397	398

### 4g. Transposable elements (*C. gigas* only)

#### All 5x CpGs

In [87]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {all5xCpGs} \
-b {transposableElementsCg} \
| wc -l
!echo "all 5x CpG loci overlaps with transposable elements (Cg)"

  767604
all 5x CpG loci overlaps with transposable elements (Cg)


In [88]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {all5xCpGs} \
-b {transposableElementsCg} \
> 2019-04-10-All5xCpGs-TE-Cg.txt

In [89]:
!head 2019-04-10-All5xCpGs-TE-Cg.txt

NC_007175.2	1873	1874	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	1874	1875	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	1918	1919	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	1919	1920	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	2003	2004	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	2004	2005	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_035780.1	6036	6037	NC_035780.1	RepeatMasker	similarity	5080	7289	32.5	-	.	Target "Motif:Gypsy-62_CGi-I" 2102 4631
NC_035780.1	6109	6110	NC_035780.1	RepeatMasker	similarity	5080	7289	32.5	-	.	Target "Motif:Gypsy-62_CGi-I" 2102 4631
NC_035780.1	9253	9254	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.

#### Methylated loci

In [38]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {methylatedLoci} \
-b {transposableElementsCg} \
| wc -l
!echo "methylated loci overlaps with transposable elements (Cg)"

  610208
methylated loci overlaps with transposable elements (Cg)


In [39]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {methylatedLoci} \
-b {transposableElementsCg} \
> 2019-04-10-MethLoci-TE-Cg.txt

In [40]:
!head 2019-04-10-MethLoci-TE-Cg.txt

NC_035780.1	9253	9254	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	19631	19632	NC_035780.1	RepeatMasker	similarity	19431	19866	23.3	-	.	Target "Motif:Crypton-N19_CGi" 580 1033
NC_035780.1	19741	19742	NC_035780.1	RepeatMasker	similarity	19431	19866	23.3	-	.	Target "Motif:Crypton-N19_CGi" 580 1033
NC_035780.1	41723	41724	NC_035780.1	RepeatMasker	similarity	41713	41751	10.3	+	.	Target "Motif:Helitron-N10B_CGi" 258 296
NC_035780.1	41723	41724	NC_035780.1	RepeatMasker	similarity	41719	41776	 6.9	+	.	Target "Motif:Helitron-10_CGi" 282 358
NC_035780.1	73023	73024	NC_035780.1	RepeatMasker	similarity	72892	73822	28.6	-	.	Target "Motif:Kolobok-N4_CGi" 1 925
NC_035780.1	87531	87532	NC_035780.1	RepeatMasker	similarity	87526	87837	24.3	-	.	Target "Motif:DNA3-12_CGi" 60 378
NC_035780.1	87541	87542	NC_035780.1	RepeatMasker	similarity	87526	87837	24.3	-	.	Target "Motif:DNA3-12_CGi" 60 378
NC_035780.1	87590	87591	NC_035780.1	RepeatMasker	similarity	

#### Sparsely methylated loci

In [51]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {sparselyMethylatedLoci} \
-b {transposableElementsCg} \
| wc -l
!echo "sparsely methylated loci overlaps with transposable elements (Cg)"

  108858
sparsely methylated loci overlaps with transposable elements (Cg)


In [52]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {sparselyMethylatedLoci} \
-b {transposableElementsCg} \
> 2019-04-10-SparseMethLoci-TE-Cg.txt

In [53]:
!head 2019-04-10-SparseMethLoci-TE-Cg.txt

NC_035780.1	9254	9255	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9266	9267	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9267	9268	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9297	9298	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9298	9299	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9301	9302	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	9302	9303	NC_035780.1	RepeatMasker	similarity	9223	9562	26.9	-	.	Target "Motif:DNA-19_CGi" 1 332
NC_035780.1	41739	41740	NC_035780.1	RepeatMasker	similarity	41713	41751	10.3	+	.	Target "Motif:Helitron-N10B_CGi" 258 296
NC_035780.1	41739	41740	NC_035780.1	RepeatMasker	similarity	41719	41776	 6.9	+	.	Target "Motif:Helitron-10_CGi" 282

#### Unmethylated loci

In [54]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {unmethylatedLoci} \
-b {transposableElementsCg} \
| wc -l
!echo "unmethylated loci overlaps with transposable elements (Cg)"

   48538
unmethylated loci overlaps with transposable elements (Cg)


In [55]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {unmethylatedLoci} \
-b {transposableElementsCg} \
> 2019-04-10-UnMethLoci-TE-Cg.txt

In [56]:
!head 2019-04-10-UnMethLoci-TE-Cg.txt

NC_007175.2	1873	1874	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	1874	1875	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	1918	1919	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	1919	1920	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	2003	2004	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_007175.2	2004	2005	NC_007175.2	RepeatMasker	similarity	1866	2013	33.6	+	.	Target "Motif:LSU-rRNA_Cel" 2372 2520
NC_035780.1	6036	6037	NC_035780.1	RepeatMasker	similarity	5080	7289	32.5	-	.	Target "Motif:Gypsy-62_CGi-I" 2102 4631
NC_035780.1	6109	6110	NC_035780.1	RepeatMasker	similarity	5080	7289	32.5	-	.	Target "Motif:Gypsy-62_CGi-I" 2102 4631
NC_035780.1	25242	25243	NC_035780.1	RepeatMasker	similarity	24971	26871	22.1

### 4h. Putative promoters

#### All 5x CpGs

In [90]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {all5xCpGs} \
-b {putativePromoters} \
| wc -l
!echo "all 5x CpG loci overlaps with putative promoters"

  203376
all 5x CpG loci overlaps with putative promoters


In [91]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {all5xCpGs} \
-b {putativePromoters} \
> 2019-04-10-All5xCpGs-Putative-Promoters.txt

In [92]:
!head 2019-04-10-All5xCpGs-Putative-Promoters.txt

NC_035780.1	27969	27970	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	27979	27980	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	28082	28083	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:1

#### Methylated loci

In [41]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {methylatedLoci} \
-b {putativePromoters} \
| wc -l
!echo "methylated loci overlaps with putative promoters"

  134534
methylated loci overlaps with putative promoters


In [42]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {methylatedLoci} \
-b {putativePromoters} \
> 2019-04-10-MethLoci-Putative-Promoters.txt

In [43]:
!head 2019-04-10-MethLoci-Putative-Promoters.txt

NC_035780.1	27969	27970	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	27979	27980	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	28082	28083	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:1

#### Sparsely methylated loci

In [57]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {sparselyMethylatedLoci} \
-b {putativePromoters} \
| wc -l
!echo "sparsely methylated loci overlaps with putative promoters"

   27443
sparsely methylated loci overlaps with putative promoters


In [58]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {sparselyMethylatedLoci} \
-b {putativePromoters} \
> 2019-04-10-SparseMethLoci-Putative-Promoters.txt

In [59]:
!head 2019-04-10-SparseMethLoci-Putative-Promoters.txt

NC_035780.1	42254	42255	NC_035780.1	Gnomon	mRNA	42111	43110	.	-	.	ID=rna2;Parent=gene2;Dbxref=GeneID:111110729,Genbank:XM_022447324.1;Name=XM_022447324.1;gbkey=mRNA;gene=LOC111110729;model_evidence=Supporting evidence includes similarity to: 1 Protein%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments;product=FMRFamide receptor-like%2C transcript variant X1;transcript_id=XM_022447324.1
NC_035780.1	42254	42255	NC_035780.1	Gnomon	mRNA	42111	43110	.	-	.	ID=rna3;Parent=gene2;Dbxref=GeneID:111110729,Genbank:XM_022447333.1;Name=XM_022447333.1;gbkey=mRNA;gene=LOC111110729;model_evidence=Supporting evidence includes similarity to: 1 Protein%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 14 samples with support for all annotated introns;product=FMRFamide receptor-like%2C transcript variant X2;transcript_id=XM_022447333.1
NC_035780.1	42358	42359	NC_035780.1	Gnomon	mRNA	42111	43110	.	-	.	ID=rna2;Parent=gene2;Dbxref=GeneID:111110

#### Unmethylated loci

In [60]:
! {bedtoolsDirectory}intersectBed \
-u \
-a {unmethylatedLoci} \
-b {putativePromoters} \
| wc -l
!echo "unmethylated loci overlaps with putative promoters"

   41399
unmethylated loci overlaps with putative promoters


In [61]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {unmethylatedLoci} \
-b {putativePromoters} \
> 2019-04-10-UnMethLoci-Putative-Promoters.txt

In [62]:
!head 2019-04-10-UnMethLoci-Putative-Promoters.txt

NC_035780.1	28859	28860	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	28924	28925	NC_035780.1	Gnomon	mRNA	27961	28960	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1
NC_035780.1	42233	42234	NC_035780.1	Gnomon	mRNA	42111	43110	.	-	.	ID=rna2;Parent=gene2;Dbxref=GeneID:1

### 4i. No overlaps

#### All 5x CpGs

In [93]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {all5xCpGs} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
| wc -l
!echo "all 5x CpG loci do not overlap with exons, introns, transposable elements (all), or putative promoters"

  627257
all 5x CpG loci do not overlap with exons, introns, transposable elements (all), or putative promoters


In [94]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {all5xCpGs} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
> 2019-04-10-All5xCpGs-NoOverlaps.txt

In [95]:
!head 2019-04-10-All5xCpGs-NoOverlaps.txt

NC_007175.2	48	49
NC_007175.2	49	50
NC_007175.2	50	51
NC_007175.2	51	52
NC_007175.2	87	88
NC_007175.2	88	89
NC_007175.2	146	147
NC_007175.2	147	148
NC_007175.2	173	174
NC_007175.2	192	193


#### Methylated loci

In [44]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {methylatedLoci} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
| wc -l
!echo "methylated loci do not overlap with exons, introns, transposable elements (all), or putative promoters"

  386003
methylated loci do not overlap with exons, introns, transposable elements (all), or putative promoters


In [45]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {methylatedLoci} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
> 2019-04-10-MethLoci-NoOverlaps.txt

In [46]:
!head 2019-04-10-MethLoci-NoOverlaps.txt

NC_035780.1	9637	9638
NC_035780.1	9657	9658
NC_035780.1	10089	10090
NC_035780.1	10331	10332
NC_035780.1	11692	11693
NC_035780.1	11706	11707
NC_035780.1	11711	11712
NC_035780.1	12686	12687
NC_035780.1	12758	12759
NC_035780.1	13486	13487


#### Sparsely methylated loci

In [63]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {sparselyMethylatedLoci} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
| wc -l
!echo "sparsely methylated loci do not overlap with exons, introns, transposable elements (all), or putative promoters"

   86923
sparsely methylated loci do not overlap with exons, introns, transposable elements (all), or putative promoters


In [64]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {sparselyMethylatedLoci} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
> 2019-04-10-SparseMethLoci-NoOverlaps.txt

In [65]:
!head 2019-04-10-SparseMethLoci-NoOverlaps.txt

NC_007175.2	1506	1507
NC_007175.2	4841	4842
NC_007175.2	13069	13070
NC_035780.1	421	422
NC_035780.1	1101	1102
NC_035780.1	1540	1541
NC_035780.1	3468	3469
NC_035780.1	9789	9790
NC_035780.1	9832	9833
NC_035780.1	9854	9855


#### Unmethylated loci

In [66]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {unmethylatedLoci} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
| wc -l
!echo "unmethylated loci do not overlap with exons, introns, transposable elements (all), or putative promoters"

  154331
unmethylated loci do not overlap with exons, introns, transposable elements (all), or putative promoters


In [67]:
! {bedtoolsDirectory}intersectBed \
-v \
-a {unmethylatedLoci} \
-b {exonList} {intronList} {transposableElementsAll} {putativePromoters} \
> 2019-04-10-UnMethLoci-NoOverlaps.txt

In [68]:
!head 2019-04-10-UnMethLoci-NoOverlaps.txt

NC_007175.2	48	49
NC_007175.2	49	50
NC_007175.2	50	51
NC_007175.2	51	52
NC_007175.2	87	88
NC_007175.2	88	89
NC_007175.2	146	147
NC_007175.2	147	148
NC_007175.2	173	174
NC_007175.2	192	193
